# DuckDB & Spatial extension example

In [2]:
!pip install lonboard duckdb==1.1.1 -q

In [3]:
import duckdb

# Initialize DuckDB connection
con = duckdb.connect()

# Load spatial extension
con.sql('INSTALL spatial;')
con.sql('LOAD spatial;')

# URL for France data
poi_url = 'https://api-01.openchargemap.io/v3/poi?client=ocm-data-export&maxresults=100000&compact=true&verbose=false&boundingbox=(51.124,-5.142),(41.342,9.562)'

# Ingest the data from the API and create as a table
con.sql(f"CREATE TABLE poi_france AS SELECT * FROM read_json_auto('{poi_url}')")


FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

In [4]:
rel = con.sql('FROM poi_france limit 5;')

In [5]:
rel.explain()

''

In [6]:
# Transform and query data
sql = """
SELECT
    ID,
    ST_Point(AddressInfo.Longitude, AddressInfo.Latitude) as geom,
    AddressInfo.Title AS Title
FROM
    poi_france
WHERE
    AddressInfo.Latitude IS NOT NULL
    AND AddressInfo.Longitude IS NOT NULL
"""

# Execute the query and fetch results
query = con.sql(sql)

In [7]:
query.explain()

''

In [8]:
# Diplay the data
from lonboard import Map, HeatmapLayer

layer = HeatmapLayer.from_duckdb(query, con)
m = Map(layer)
m

/usr/local/lib/python3.10/dist-packages/lonboard/_layer.py:1984: UserWarning: 
The `HeatmapLayer` is not currently working.

As of Lonboard v0.10, Lonboard upgraded to version 9.0 of the underlying
[deck.gl](https://deck.gl/) library. deck.gl [appears to have a
bug](https://github.com/visgl/deck.gl/issues/8960#issuecomment-2284791644) with
the HeatmapLayer in 9.0, that has not yet been fixed.

Please temporarily downgrade to Lonboard v0.9 if you would like to use the
`HeatmapLayer`.

  warnings.warn(dedent(err_msg), UserWarning)
/usr/local/lib/python3.10/dist-packages/lonboard/_geoarrow/ops/reproject.py:33: UserWarning: No CRS exists on data. If no data is shown on the map, double check that your CRS is WGS84.
  warn(


Map(custom_attribution='', layers=(HeatmapLayer(table=arro3.core.Table
-----------
ID: Int64
Title: Utf8
geome…

# Using with MotherDuck

You can create an account for free at [motherduck.com](https://www.motherduck.com/) and [retrieve your token to authenticate](https://motherduck.com/docs/key-tasks/authenticating-and-connecting-to-motherduck/authenticating-to-motherduck/#authentication-using-an-access-token) through the UI. Once done, inside the Collab notebook go to the left side panel > secrets and fill your `motherduck_token` value.

In [9]:
# populating motherduck_token as en env.
from google.colab import userdata
import os
os.environ['motherduck_token']=userdata.get('motherduck_token')

SecretNotFoundError: Secret motherduck_token does not exist.

In [ ]:
import duckdb

# Initialize DuckDB connection
con = duckdb.connect('md:')

# Load spatial extension
con.sql('INSTALL spatial;')
con.sql('LOAD spatial;')

# URL for France data
poi_url = 'https://api-01.openchargemap.io/v3/poi?client=ocm-data-export&maxresults=100000&compact=true&verbose=false&boundingbox=(51.124,-5.142),(41.342,9.562)'

# Ingest the data from the API and create as a table
# Create database if not exist
con.sql("CREATE DATABASE IF NOT EXISTS geo_playground")
con.sql(f"CREATE TABLE IF NOT EXISTS geo_playground.poi_france AS SELECT * FROM read_json_auto('{poi_url}')")


In [ ]:
con.sql('show databases;')

┌────────────────────────┐
│     database_name      │
│        varchar         │
├────────────────────────┤
│ dataskills_radar       │
│ duckdb_in_action_ch3_4 │
│ duckdb_stats           │
│ duckrel                │
│ duckrel2               │
│ geo_demo               │
│ geo_playground         │
│ huggingface_dataset    │
│ mosaic_examples        │
│ playground             │
│ pypi_history           │
│ remote_tpch            │
│ sample_data            │
│ test_backup            │
│ tpch                   │
├────────────────────────┤
│        15 rows         │
└────────────────────────┘

In [ ]:
# Uploading the current local table to MotherDuck
sql = """ CREATE TABLE IF NOT EXISTS geo_playground.poi_france_display AS
SELECT
    ID,
    ST_Point(AddressInfo.Longitude, AddressInfo.Latitude) as geom,
    AddressInfo.Title AS Title
FROM
    geo_playground.poi_france
WHERE
    AddressInfo.Latitude IS NOT NULL
    AND AddressInfo.Longitude IS NOT NULL
"""
con.sql(sql)

In [ ]:
# This query run in MotherDuck Cloud
con.sql('FROM geo_playground.poi_france_display limit 5')

┌────────┬───────────────────────────────────────────────┬─────────────────────────────┐
│   ID   │                     geom                      │            Title            │
│ int64  │                   geometry                    │           varchar           │
├────────┼───────────────────────────────────────────────┼─────────────────────────────┤
│ 203362 │ POINT (-5.075207325926755 43.448421243964304) │ Hotel Rural La Curva        │
│ 299450 │ POINT (-5.06783854990374 43.465030087046614)  │ Hotel Villa Rosario         │
│ 209224 │ POINT (-5.06419388654615 43.46594466895118)   │ Gran Hotel del Sella        │
│ 201363 │ POINT (-5.062485285379808 43.43078297825821)  │ Rest. Canoas La Ribera      │
│ 194441 │ POINT (-5.129921424610529 43.348744254371155) │ Hotel Cangas de Onis Center │
└────────┴───────────────────────────────────────────────┴─────────────────────────────┘

In [ ]:
# Diplay the data
from lonboard import Map, HeatmapLayer

# Directly query from MotherDuck store table
query = con.sql("SELECT * FROM geo_playground.poi_france_display")
layer = HeatmapLayer.from_duckdb(query, con)
m = Map(layer)
m

/usr/local/lib/python3.10/dist-packages/lonboard/_geoarrow/ops/reproject.py:23: UserWarning: No CRS exists on data. If no data is shown on the map, double check that your CRS is WGS84.
  warn(


Map(layers=[HeatmapLayer(table=pyarrow.Table
ID: int64
Title: string
geometry: fixed_size_list<item: double>[2…

# Share your dataset

In [ ]:
# Create a MotherDuck Share to share with other MotherDuck users
con.sql("CREATE SHARE IF NOT EXISTS ev_poi_france FROM geo_playground (ACCESS UNRESTRICTED);")


┌──────────────────────────────────────────────────────────────┐
│                          share_url                           │
│                           varchar                            │
├──────────────────────────────────────────────────────────────┤
│ md:_share/ev_poi_france/9885fb77-4a2d-45ff-a321-98514cd06b69 │
└──────────────────────────────────────────────────────────────┘

In [ ]:
# Export to geojson
con.sql("COPY geo_playground.poi_france_display TO './ev_poi_france.geojson' WITH (FORMAT GDAL, DRIVER 'GeoJSON');")